In [1]:
import pandas as pd
import numpy
import jieba
import os
from threading import Thread
import time
from os import walk
import codecs
from datetime import datetime
from elasticsearch import Elasticsearch
from elasticsearch.helpers import bulk
from time import time
import os
import sys
import fnmatch
import win32com.client
PATH = os.path.abspath(os.path.dirname(sys.argv[0]))
#print(PATH)
PATH_DATA=r'E:\Desktop_xsj\Desktop\Workshop\1G'

'''2.	Then the effect of our map reduce on django is very poor. 
Although it has processed the data into a very considerable form, 
it still needs to traverse the huge rdd table structure 
when the user searches, and its index is not obtained. Very good optimization, so the search takes a long time.'''

In [1]:
# This function is only used for basic format conversion
def docx_to_text():
    wordapp = win32com.client.\
        gencache.EnsureDispatch("Word.Application")
    try:
        for root, dirs, files\
                in os.walk(PATH_DATA):
            print(root,dirs,files)
            for _dir in dirs: 
                pass
            for _file in files:  
                if not fnmatch.\
                        fnmatch(_file, '*.docx'):
                    continue
                word_file = os.path.join(root, _file)
                wordapp.Documents.Open(word_file)
                docastxt = word_file[:-4] + 'txt'
                wordapp.ActiveDocument\
                    .SaveAs(
                    docastxt,
                    FileFormat=
                    win32com.client.constants.wdFormatText)
                wordapp.ActiveDocument.Close()
    finally:
        wordapp.Quit()
        

# This function is very important
def readfile():
    docx_name=[]   # To store The document / file name
    filename=[] 
    all_file=[]   
    content=[]
    x=-1
    try:
        for root, dirs, files in os.walk(PATH_DATA):
            temp_content = []
            for every_docx_name in files:
                # print('hang',hang)
                every_file_path = \
                    os.path.join(root, every_docx_name)
            # Here we can make some process like split, merge
            # or other some operation to get the feature we want
            with codecs.open(every_file_path, encoding='utf-8') as f:
                temp = f.read()
                attribute=every_docx_name.split("_")
                book_name=attribute[0]
                author_lst=attribute[1][:-4]
                print("===================")
                print(author_lst)
                # Here we just get the bookname, author, and the contect of text
                wy.Index_Data(filename[x],book_name,author_lst,tempcishu)
                    
 
class ElasticWy:
    def __init__(self, index_name,ip ="localhost"):
        self.index_name = index_name
        self.es = Elasticsearch([ip], port=9200)
    def create_index(self,index_name):
        _index_mappings = {
            "mappings": {
                    "properties": {
                        "source": {
                            "type": "text",
                            "index": True,
                            "analyzer": "ik_max_word",
                            "search_analyzer": "ik_max_word"
                        }
                    }
            }
        }
        if self.es.indices.exists(index=self.index_name) is not True:
            res = self.es.indices.create(index=self.index_name, body=_index_mappings)
            
    def ReadFile(self,filepath):
        # filepath='C:\\Users\\wy\\Desktop\\data' \
        #          '\\elasticsearch\\data.txt'
        if os.path.exists(filepath) and os.path.isfile(filepath):
            with open(filepath) as f:
                temp_list=[]
                for line in f:
                    temp_set={}
                    #print(line)
                    temp_set=str(line)
                    temp_list.append(temp_set)
                #print(temp_list)
            return temp_list
    
    # Index_Data is the function we called in the load file
    # we can define the attrubute for our book information
    def Index_Data(self,category,book_name,author_lst,content,cishu):
        if isinstance(content,str):
            action = {
                    'category': category,
                    'name': book_name,
                    'author_lst': author_lst,
                    "title": content}
                          body=action)
    
    
    # finially we define the way for our search 
    # under the match, we set the what attribute we what to search by
    def Search_name(self,input_text):
        
        doc = {
            "query": {
                "match":{
                    "name": {
                            "query": input_text,
                            "operator": "and"
                    }
                }
            }
        }
        _searched = self.es.search(
            index=self.index_name,
            body=doc)
        i=0
        last_author = []
        last_category = []
        last_docxname = []
        last_sentence = []
        
        # After load the book text and insert index, all the attribute information will store in the a two dimesnsion dictionaries.
        # we can get the same tuple of the search item, include other attributes, TFIDF score and the word position in the text
        for hit in _searched['hits']['hits']:
            print (hit['_source'])
            last_category.append(hit['_source']['category'])
            last_docxname.append(hit['_source']['name'])
            last_author.append(hit['_source']['author_lst'])
            last_sentence.append(hit['_source']['title'])
            
            i=i+1
            if i==20:
                break

        print(last_docxname)
        print("=============")
 
    # search by word in the text file
    def Search_data(self,input_text):
        doc = {
            "query": {
                "match":{
                    "title": {
                            "query": input_text,
                            "operator": "and"
                    }
                }
            }
        }
        _searched = self.es.search(
            index=self.index_name,
            body=doc)
        i=0
        last_author = []
        last_category = []
        last_docxname = []
        last_sentence = []
        for hit in _searched['hits']['hits']:
            last_category.append(hit['_source']['category'])
            last_docxname.append(hit['_source']['name'])
            last_author.append(hit['_source']['author_lst'])
            last_sentence.append(hit['_source']['title'])
            i=i+1
            if i==20:
                break
        #print(len(last_sentence))
#         for temp in last_sentence:
#             print(temp)
        print(last_docxname)
        #cost_time = time()-start_time
        #print(cost_time)
    
    def Search_author(self,input_text):
        doc = {
            "query": {
                "match":{
                    "author_lst": {
                            "query": input_text,
                            "operator": "and"
                    }
                }
                'content':True,
                'topN':20,
            }
        }
        _searched = self.es.search(
            index=self.index_name,
            body=doc)
        i=0
        last_author = []
        last_category = []
        last_docxname = []
        last_sentence = []
        for hit in _searched['hits']['hits']:
            print (hit['_source'])
            #print ( hit['_source']['title'])
            # print(hit['_score'])
            last_category.append(hit['_source']['category'])
            last_docxname.append(hit['_source']['name'])
            last_author.append(hit['_source']['author_lst'])
            last_sentence.append(hit['_source']['title'])
            i=i+1
            if i==20:
                break


In [15]:
# instantiation the class
wy = ElasticWy("Jack", ip="localhost")
wy.create_index(index_name="Jack")

jojo


In [16]:
readfile()

文件开始读取
已经读取到 book 文件夹
gbk: 1492_Mary Johnsto.txt
Mary Johnsto
已经插入 1 条记录
gbk: 1601_Mark Twai.txt
Mark Twai
已经插入 2 条记录
gbk: A Bit O' Love (Fourth Series Plays)_John Galsworth.txt
John Galsworth
已经插入 3 条记录
gbk: A Blot In The 'Scutcheon_Robert Brownin.txt
Robert Brownin
已经插入 4 条记录
gbk: A Book of Scoundrels_Charles Whible.txt
Charles Whible
已经插入 5 条记录
gbk: A Book of Scoundrels_Whibley Charle.txt
Whibley Charle


<ipython-input-14-50001106383a>:197: DeprecationWarning: The 'body' parameter is deprecated for the 'index' API and will be removed in a future version. Instead use the 'document' parameter. See https://github.com/elastic/elasticsearch-py/issues/1698 for more information
  self.es.index(index=self.index_name,


已经插入 6 条记录
gbk: A Book of Strife in the Form of The Diary of an Old Soul_George MacDonal.txt
George MacDonal
已经插入 7 条记录
gbk: A Book of Strife in the Form of The Diary of an Old Soul_MacDonald Georg.txt
MacDonald Georg
已经插入 8 条记录
gbk: A Boy's Will_Robert Fros.txt
Robert Fros
已经插入 9 条记录
gbk: A Bundle of Ballads_Variou.txt
Variou
已经插入 10 条记录
gbk: A Bundle of Letters_Henry Jame.txt
Henry Jame
已经插入 11 条记录
gbk: A Burlesque Autobiography_Mark Twain (Samuel Clemens.txt
Mark Twain (Samuel Clemens
已经插入 12 条记录
gbk: A Cathedral Courtship_Kate Douglas Wiggi.txt
Kate Douglas Wiggi
已经插入 13 条记录
gbk: A Cathedral Courtship_Wiggin Kate Douglas Smit.txt
Wiggin Kate Douglas Smit
已经插入 14 条记录
gbk: A Changed Man and Other Tales_Thomas Hard.txt
Thomas Hard
已经插入 15 条记录
gbk: Andrea Delfin_ Paul Heys.txt
 Paul Heys
已经插入 16 条记录
gbk: Captains Courageous   A Story of the Grand Banks_Kipling Rudyar V1.txt
Kipling Rudyar V1
已经插入 17 条记录
gbk: Captains Courageous   A Story of the Grand Banks_Kipling Rudyar.txt
Kipling Ru

In [17]:
while(1):
        print("input the word you want to sarch")
        input_text = input()
        if input_text != str(0):
            print('the serach result: ')
            res = wy.Search_data(input_text=input_text)
        else:
            break


请输入与要匹配的字符串,输入 0 终止查询
0
查询终止


In [6]:
while(1):
        print("input the word you want to sarch")
        input_text = input()
        if input_text != str(0):
            print('result: ')
            res = wy.Search_name(input_text=input_text)
        else:
            break


请输入与要匹配的字符串,输入 0 终止查询
group


<ipython-input-2-7187c5d8d5b4>:216: DeprecationWarning: The 'body' parameter is deprecated for the 'search' API and will be removed in a future version. Instead use API parameters directly. See https://github.com/elastic/elasticsearch-py/issues/1698 for more information
  _searched = self.es.search(


查询结果如下
[]
[]
请输入与要匹配的字符串,输入 0 终止查询
Captains
查询结果如下
{'category': 'book', 'name': 'Captains Courageous ', 'author_lst': 'Rudyard Kiplin V1', 'title': 'The Project Gutenberg EBook of "Captains Courageous", by Rudyard Kipling\r\r\n\r\r\nThis eBook is for the use of anyone anywhere at no cost and with\r\r\nalmost no restrictions whatsoever.  You may copy it, give it away or\r\r\nre-use it under the terms of the Project Gutenberg License included\r\r\nwith this eBook or online at www.gutenberg.org\r\r\n\r\r\n\r\r\nTitle: "Captains Courageous"\r\r\n\r\r\nAuthor: Rudyard Kipling\r\r\n\r\r\nRelease Date: October 4, 1999 [EBook #2225]\r\r\nLast updated: February 18, 2018\r\r\n\r\r\nLanguage: English\r\r\n\r\r\n\r\r\n*** START OF THIS PROJECT GUTENBERG EBOOK "CAPTAINS COURAGEOUS" ***\r\r\n\r\r\n\r\r\n\r\r\n\r\r\nProduced by Bill Stoddard.\r\r\n\r\r\n\r\r\n\r\r\n\r\r\n"CAPTAINS COURAGEOUS"\r\r\n\r\r\nA STORY OF THE GRAND BANKS\r\r\n\r\r\nBy Rudyard Kipling\r\r\n\r\r\n\r\r\n\r\r\n\r\r\nCHAPTER I\r\

KeyboardInterrupt: Interrupted by user

In [ ]:
while(1):
        print("input you want to search")
        input_text = input()
        if input_text != str(0):
            print('The query result')
            res = wy.Search_author(input_text=input_text)
        else:
            break


请输入与要匹配的字符串,输入 0 终止查询
jack
查询结果如下


<ipython-input-14-50001106383a>:302: DeprecationWarning: The 'body' parameter is deprecated for the 'search' API and will be removed in a future version. Instead use API parameters directly. See https://github.com/elastic/elasticsearch-py/issues/1698 for more information
  _searched = self.es.search(


[]
请输入与要匹配的字符串,输入 0 终止查询
John
查询结果如下
{'category': 'book', 'name': "A Bit O' Love (Fourth Series Plays)", 'author_lst': 'John Galsworth', 'title': '\r\r\n Project Gutenberg\'s A Bit O\' Love (Fourth Series Plays), by John Galsworthy\r\r\n\r\r\n This eBook is for the use of anyone anywhere at no cost and with\r\r\n almost no restrictions whatsoever.  You may copy it, give it away or\r\r\n re-use it under the terms of the Project Gutenberg License included\r\r\n with this eBook or online at www.gutenberg.org\r\r\n\r\r\n\r\r\n Title: A Bit O\' Love (Fourth Series Plays)\r\r\n\r\r\n Author: John Galsworthy\r\r\n\r\r\n Release Date: September 26, 2004 [EBook #2915]\r\r\n\r\r\n Language: English\r\r\n\r\r\n Character set encoding: ASCII\r\r\n\r\r\n *** START OF THIS PROJECT GUTENBERG EBOOK A BIT O\' LOVE (FOURTH SERIES ***\r\r\n\r\r\n\r\r\n\r\r\n\r\r\n Produced by David Widger\r\r\n\r\r\n\r\r\n\r\r\nPLAYS IN THE FOURTH SERIES\r\r\n\r\r\n\r\r\nA BIT O\' LOVE\r\r\n\r\r\nBy John Galsworthy\r\r\n

In [1]:
a = [1,2,3]
b = [4,5,6]
c = [7,8,9]

In [8]:
zipped = zip(a, b, c)

In [11]:
print(list(zipped))

[(1, 4, 7), (2, 5, 8), (3, 6, 9)]
